This notebook is module 1 of NEKO.

It does the following steps:
1. Search PubMed and save an article list.
2. IUse LLM to identify causal relationships between knowledge entities.
3. Remove repetitive entities.
4. Plot all entities on a knowledge graph using Pyvis.

To use this notebook, you need to:

- Input the path to Qwen model (from huggingface or from local storage).
- Input your Email to use NCBI Entrez PubMed search API.
- Set the maximum number of search results.
- Input your search keyword.
- Modify the prompt according to your needs.


In [1]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0,1,2,3"

from transformers import AutoModelForCausalLM, AutoTokenizer
device = "cuda" # the device to load the model onto

model = AutoModelForCausalLM.from_pretrained("/storage1/fs1/yinjie.tang/Active/Shawn_Xiao/Qwen1.5-72B-Chat",
    device_map="auto", torch_dtype="auto"
)
tokenizer = AutoTokenizer.from_pretrained("/storage1/fs1/yinjie.tang/Active/Shawn_Xiao/Qwen1.5-72B-Chat")

#Qwen1.5-72B-Chat
#Qwen1.5-14B-Chat

Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [2]:
# Search PubMed and get article abstracts

# pip install biopython pandas openpyxl

from Bio import Entrez
import pandas as pd

# Define your email to use with NCBI Entrez
Entrez.email = "your_email@sample.com"
#****** Add your search keyword here ******
keyword = "rhodococcus"

def search_pubmed(keyword):
    
    # Adjust the search term to focus on abstracts
    search_term = f"{keyword}[Abstract]"
    handle = Entrez.esearch(db="pubmed", term=search_term, retmax=300)
    record = Entrez.read(handle)
    handle.close()

    # Get the list of Ids returned by the search
    id_list = record["IdList"]
    return id_list

def fetch_details(id_list):
    ids = ','.join(id_list)
    handle = Entrez.efetch(db="pubmed", id=ids, retmode="xml")
    records = Entrez.read(handle)
    handle.close()

    # Create a list to hold our article details
    articles = []

    for pubmed_article in records['PubmedArticle']:
        article = {}
        article_data = pubmed_article['MedlineCitation']['Article']
        article['Title'] = article_data.get('ArticleTitle')
        
        # Directly output the abstract
        abstract_text = article_data.get('Abstract', {}).get('AbstractText', [])
        if isinstance(abstract_text, list):
            abstract_text = ' '.join(abstract_text)
        article['Abstract'] = abstract_text

        article['Journal'] = article_data.get('Journal', {}).get('Title')

        articles.append(article)

    return articles

id_list = search_pubmed(keyword)
articles = fetch_details(id_list)

# Convert our list of articles to a DataFrame
df = pd.DataFrame(articles)

# Saving the DataFrame to an Excel file
excel_filename = keyword+"_pubmed_search_results.xlsx"
df.to_excel(excel_filename, index=False)

print(f"Saved search results to {excel_filename}")


Saved search results to rhodococcus_pubmed_search_results.xlsx


In [3]:
# Qwen reads abstract and identify knowledge
import pandas as pd
import os
import torch

# Function to interact with the LLM API using the new method, now with customizable system prompts
def ask_questions(abstract, questions, system_prompts):
    responses = []
    for question, system_prompt in zip(questions, system_prompts):
        # Combine the question and abstract to form the prompt
        prompt_text = question + " " + str(abstract)
        
        messages = [
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": prompt_text}
        ]
        text = tokenizer.apply_chat_template(
            messages,
            tokenize=False,
            add_generation_prompt=True
        )
        model_inputs = tokenizer([text], return_tensors="pt").to(device)
        
        # Generate response with the API
        generated_ids = model.generate(
            model_inputs.input_ids,
            max_new_tokens=5000
        )
        generated_ids = [
            output_ids[len(input_ids):] for input_ids, output_ids in zip(model_inputs.input_ids, generated_ids)
        ]
        
        # Decode the generated response
        response = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)[0]
        responses.append(response)
    return responses

# Read the Excel file
file_path = excel_filename 
df = pd.read_excel(file_path)

# Define your questions and system prompts
questions = [
    " ",
    " "
]  # Update questions as needed

system_prompts = [
    "What is the main findings and conclusions in this study? Answer with 1 concise sentence.",
    "You are specialized for analyzing scientific paper abstracts, focusing on identifying entities causal relationships related to biological studies, such as performance, species, genes, methods of genetic engineering, enzymes, proteins, and bioprocess conditions (e.g., growth conditions). It outputs the identified causal relationships between entities in combination pairs. The output strictly follows the format: (Entity A, Entity B), (Entity C, Entity D) ... with no additional text."
]  # Define system prompts corresponding to each question

# Process each abstract and store the responses
total_rows = len(df)
for i, row in df.iterrows():
    # Clear the console at the beginning of each iteration
    os.system('cls' if os.name == 'nt' else 'clear')

    responses = ask_questions(row['Abstract'], questions, system_prompts)
    df.at[i, 'Answer to Question 1'] = responses[0]
    df.at[i, 'Answer to Question 2'] = responses[1]

    # Show the responses
    print(f"Responses for Row {i+1}:")
    for j, response in enumerate(responses):
        print(f"Response to {questions[j]}: {response}")

    # Calculate and show the progress percentage
    progress = ((i + 1) / total_rows) * 100
    print(f"Progress: {progress:.2f}% completed")
    
# Save the updated DataFrame back to an Excel file
output_file_path = 'updated(Qwen1.5 72B)_'+keyword+'_causal.xlsx'  # Replace with your desired output file path
df.to_excel(output_file_path, index=False)


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Responses for Row 1:
Response to  : This study found a high prevalence of various antibiotic resistance genes in Lake Cajititlán, with Pseudomonas and Stenotrophomonas species having the highest frequencies, posing a risk to human and environmental health, emphasizing the need for improved wastewater treatment and responsible antibiotic use.
Response to  : (Anthropogenic sources, antibiotic resistance genes), (Lake Cajititlán, bacterial genera), ('Pseudomonas', antibiotic resistance genes), ('Stenotrophomonas', antibiotic resistance genes), ('Mycobacterium', antibiotic resistance genes), ('Rhodococcus', antibiotic resistance genes), ('Pseudomonas aeruginosa', antibiotic resistance genes), ('Stenotrophomonas maltophilia', antibiotic resistance genes), ('macrolides', antibiotic resistance), ('aminoglycosides', antibiotic resistance), ('glycopeptides', antibiotic resistance), ('tetracyclines', antibiotic resistance), ('sulfonamides', antibiotic resistance), ('carbapenems', antibiotic resi

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Responses for Row 2:
Response to  : The study found that certain bacterial strains, particularly Streptomyces fulvissimus (SF) and its co-culture with Rhodococcus jostii (RJ), can potentially degrade polylactic acid (PLA) plastic film at higher temperatures, suggesting their potential as accelerators of PLA degradation but highlighting the need for further research on soil bioremediation.
Response to  : (Mycobacterium vanbaalenii (MV), plastic debris), (Rhodococcus jostii (RJ), low-density polyethylene film (LDPE-f)), (Streptomyces fulvissimus (SF), polylactic acid (PLA-f)), (Bacillus simplex (BS), polybutylene adipate terephthalate film (PBAT-f)), (Sporosarcina globispora (SG), Bionov-B), (PLA-f, Mycobacterium vanbaalenii (MV)), (PLA-f, Rhodococcus jostii (RJ)), (PLA-f, Streptomyces fulvissimus (SF)), (PLA-f, Bacillus simplex (BS)), (PLA-f, Sporosarcina globispora (SG)), (PLA-f, Bionov-B), (Streptomyces fulvissimus (SF), PLA-f), (temperature, PLA degradation), (30 °C, PLA degradation)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


...

Responses for Row 4997:
Response to  : The study identified a divergently transcribed gene, CatR, upstream of the catechol 1,2-dioxygenase gene catA in Rhodococcus opacus 1CP, which belongs to the PobR subfamily of regulatory proteins and may be involved in catechol catabolism regulation,不同于 previously known LysR-type regulators.
Response to  : (Rhodococcus opacus 1CP, pRER1), (pRER2, DNA fragment), (pRER2, catABC), (catA, catechol 1,2-dioxygenase gene), (CatR, gene upstream of catA), (CatR, PobR subfamily), (proteobacteria, LysR-type regulators), (catR, catA intergenic region), (CatR, regulation of catechol catabolism)
Progress: 99.96% completed


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Responses for Row 4998:
Response to  : This study highlights the potent biosurfactant properties of glycolipids produced by Rhodococcus bacteria, their potential industrial applications due to low toxicity compared to synthetic surfactants, and the need for research on their genetic basis to reduce production costs for wider adoption in various industries, including environmental remediation.
Response to  : (Rhodococcus erythropolis, trehalose mycolates), (Rhodococcus erythropolis, anionic trehalose tetraesters), (water, surface tension), (water, interfacial tension), (n-hexadecane, interfacial tension), (biosurfactants, critical micelle concentration), (synthetic surfactants, toxicity), (biosurfactants, toxicity), (petrochemical-derived surfactants, environmental impact), (Rhodococcus, glycolipid production), (environmental remediation industries, purified molecules), (industrial applications, surfactant production).
Progress: 99.98% completed


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


Responses for Row 4999:
Response to  : This study proposes a model for the complex cell envelope of Rhodococcus, emphasizing the unique structure featuring arabinogalactan, mycolic acids, and various other components, forming a permeability barrier and suggesting implications for understanding their environmental and biotechnological applications.
Response to  : 1. (Rhodococcus cell envelope, understanding and exploitation)
2. (Rhodococcus, mycolata taxon)
3. (mycolata taxon, includes Corynebacterium, Mycobacterium, Nocardia)
4. (rhodococcal cell envelope, architectural model of mycobacterial cell envelope)
5. (rhodococcal cell envelope, arabinogalactan cell wall polysaccharide)
6. (rhodococcal cell envelope, 2-alkyl 3-hydroxy branched-chain fatty acids, mycolic acids)
7. (mycolic acids, peptidoglycan-arabinogalactan-mycolic acid matrix)
8. (outer lipid permeability barrier, mycolic acids in rhodococci)
9. (cell envelope components, localization)
10. (cell envelope components, lipoglyc

In [ ]:
# remove repeat words
import pandas as pd
import re

# Load an Excel file
df = pd.read_excel(output_file_path, engine='openpyxl')

# Fill NaN values in 'Response to New Question' column with zero
df['Answer to Question 2'] = df['Answer to Question 2'].fillna(0)

# Convert the column values to strings (to ensure compatibility with re.findall)
column_values = df['Answer to Question 2'].astype(str).tolist()

# Initialize an empty list to hold entities
entities = []

# Regular expression to match the pattern (entity A, entity B)
pattern = r'\(([^,]+), ([^\)]+)\)'

# Iterate over each cell in the column
for value in column_values:
    # Find all matches of the pattern in the cell
    matches = re.findall(pattern, value)
    # For each match, extend the entities list with the extracted entities
    for match in matches:
        entities.extend(match)  # This adds both entity A and entity B to the list

# Remove duplicates if necessary
entities = list(dict.fromkeys(entities))

# Join the entities with commas
entities_string = ', '.join(entities)

print(entities_string)

import pandas as pd
from sentence_transformers import SentenceTransformer, util

# Load your Excel file
file_path = output_file_path
df = pd.read_excel(file_path, engine='openpyxl')

# Assuming you have a list of entities and their embeddings already
entities = [entity.strip() for entity in entities_string.split(',')]
t2vmodel = SentenceTransformer('all-MiniLM-L6-v2')
embeddings = t2vmodel.encode(entities)

# Identify similar phrases and store them in a dictionary
similar_phrases = {}

# Calculate total iterations for progress tracking
total_iterations = sum(range(len(entities)))

# Initialize a counter to track progress
current_iteration = 0

for i in range(len(entities)):
    for j in range(i + 1, len(entities)):
        similarity = util.pytorch_cos_sim(embeddings[i], embeddings[j])
        if similarity.item() > 0.8:
            # Assuming entities[i] is the first phrase and entities[j] is the similar one
            similar_phrases[entities[j]] = entities[i]

        # Update the current iteration counter after each inner loop iteration
        current_iteration += 1

    # Print the percentage completed
    percentage_completed = (current_iteration / total_iterations) * 100
    print(f"Progress: {percentage_completed:.2f}%")

# Specify the column you want to modify
specific_column = 'Answer to Question 2'

# Calculate total iterations for progress tracking (only for the specific column)
total_rows = len(df)
current_iteration = 0

# Iterate through the specific column to substitute similar phrases
for index, row in df.iterrows():
    current_iteration += 1
    # Print progress every 100 rows to avoid performance degradation
    if current_iteration % 100 == 0 or current_iteration == total_rows:
        progress_percentage = (current_iteration / total_rows) * 100
        print(f"Progress: {progress_percentage:.2f}% complete.")
    
    cell_value = str(row[specific_column])
    for similar, original in similar_phrases.items():
        # Check if the phrase contains 'Yarrowia', if so, skip substitution
        if 'Yarrowia' in cell_value or 'Yarrowia' in similar:
            continue
        if similar in cell_value:
            # Substitute similar phrase with the original phrase, ignoring errors if not found
            try:
                df.at[index, specific_column] = cell_value.replace(similar, original)
            except Exception as e:
                print(f"Error substituting phrase: {e}")
                continue

# Save the modified Excel file
modified_file_path = 'modified_' + file_path
df.to_excel(modified_file_path, index=False, engine='openpyxl')

print("Excel file has been modified and saved as:", modified_file_path)
